
# Mesh manipulation

Using a mesh and modifying it while it is displayed


In [ ]:
from __future__ import absolute_import
from soma import aims
import time
import anatomist.direct.api as anatomist
import sys
from soma.qt_gui.qt_backend.QtGui import qApp
from soma.qt_gui.qt_backend import Qt
import six

# create a unit sphere of radius 1 and 500 vertices
m = aims.SurfaceGenerator.sphere(aims.Point3df(0, 0, 0), 1, 500, False)

# Multiply the sphere size by 100
for p in six.moves.xrange(m.vertex().size()):
    m.vertex()[p] *= 100

runloop = Qt.QApplication.instance() is None and 'IPython' not in sys.modules

# Open Anatomist
a = anatomist.Anatomist()

# Put the mesh in anatomist
am = a.toAObject(m)
am.releaseAppRef()

# Create a new 3D window in Anatomist
aw = a.createWindow('3D')
# c = anatomist.CreateWindowCommand( '3D' )
# proc.execute( c )
# aw = c.createdWindow()

# Put the mesh in the created window
a.addObjects(am, aw)
# c = anatomist.AddObjectCommand( [ am ], [ aw ] )
# proc.execuFalsete( c )

# keep a copy of original vertices
coords = [aims.Point3df(m.vertex()[i])
          for i in six.moves.xrange(len(m.vertex()))]
# take one vertex out of 3
points = six.moves.xrange(0, len(coords), 3)

for i in six.moves.xrange(10):
    # shrink
    for s in reversed(six.moves.xrange(100)):
        for p in points:
            m.vertex()[p] = coords[p] * s / 100.
        am.setChanged()
        am.notifyObservers()
        qApp.processEvents()
        time.sleep(0.01)
    # expand
    for s in six.moves.xrange(100):
        for p in points:
            m.vertex()[p] = coords[p] * s / 100.
        am.setChanged()
        am.notifyObservers()
        qApp.processEvents()
        time.sleep(0.01)

# display in matplotlib for sphinx_gallery
s = 0
for p in points:
    m.vertex()[p] = coords[p] * s / 100.
am.setChanged()
am.notifyObservers()
if aw.sphinx_gallery_snapshot():
    runloop = False
if runloop:
    Qt.QApplication.instance().exec_()
if runloop or 'sphinx_gallery' in sys.modules:
    del aw, am, m